# ASUM-DM

In [2]:
from ydata_profiling import ProfileReport
from pycaret.regression import *
import pandas as pd
import warnings
warnings.filterwarnings("ignore")

## Verificacion de datos

In [3]:
data=pd.read_csv('insurance.csv')
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1338 entries, 0 to 1337
Data columns (total 7 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   age       1338 non-null   int64  
 1   sex       1338 non-null   object 
 2   bmi       1338 non-null   float64
 3   children  1338 non-null   int64  
 4   smoker    1338 non-null   object 
 5   region    1338 non-null   object 
 6   charges   1338 non-null   float64
dtypes: float64(2), int64(2), object(3)
memory usage: 73.3+ KB


## Profile Report

In [3]:
profile = ProfileReport(data)

In [4]:
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Modelos - Busqueda

## Separacion entrenamiento, prediccion

In [4]:
data_model = data.sample(frac=0.9, random_state=123)
data_unseen = data.drop(data_model.index)
data_model.reset_index(inplace=True, drop=True)
data_unseen.reset_index(inplace=True, drop=True)
print('Data for Modeling: ' + str(data_model.shape))
print('Unseen Data For Predictions: ' + str(data_unseen.shape))

Data for Modeling: (1204, 7)
Unseen Data For Predictions: (134, 7)


## Configuracion experimento

In [11]:
bestRun = {
    "model": [],
    "score": []
}
currentRun = {
    "model": [],
    "score": []
}


In [12]:
import random
def update_best_run(bestRun, currentRun):
    if not bestRun["model"] and not bestRun["score"]:
        return currentRun.copy()  # Avoid reference issue
    elif calculate_average(currentRun["score"]) < calculate_average(bestRun["score"]):
        return currentRun.copy()  # Avoid reference issue
    return bestRun

def calculate_average(scores):
    if not scores:
        return 0
    return sum(scores) / len(scores)


for i in range(40):
    exp = setup(data=data_model,
                target='charges',
                session_id=random.randint(0, 10000),
                normalize=True,
                transformation=True,
                remove_multicollinearity=True,
                multicollinearity_threshold=0.9)
    
    models = compare_models(n_select=3, sort='MAPE')
    
    # Append models and their scores to currentRun
    currentRun["model"] = models
    scores = pull()['MAPE'].tolist()
    currentRun["score"] = scores[:3]

    
    # Update bestRun with the best current run
    bestRun = update_best_run(bestRun, currentRun)


In [14]:
bestRun

{'model': [PassiveAggressiveRegressor(random_state=5021),
  HuberRegressor(),
  ExtraTreesRegressor(n_jobs=-1, random_state=5021)],
 'score': [0.2301, 0.2315, 0.2343]}

## Save base models

In [18]:
save_model(bestRun["model"][0], 'PassiveAggressiveRegressor')
save_model(bestRun["model"][1], 'HuberRegressor')
save_model(bestRun["model"][2], 'ExtraTreesRegressor')

Transformation Pipeline and Model Successfully Saved
Transformation Pipeline and Model Successfully Saved
Transformation Pipeline and Model Successfully Saved


(Pipeline(memory=Memory(location=None),
          steps=[('numerical_imputer',
                  TransformerWrapper(include=['age', 'bmi', 'children'],
                                     transformer=SimpleImputer())),
                 ('categorical_imputer',
                  TransformerWrapper(include=['sex', 'smoker', 'region'],
                                     transformer=SimpleImputer(strategy='most_frequent'))),
                 ('ordinal_encoding',
                  TransformerWrapper(include=['sex', 'smoker'],
                                     transfor...
                                                               use_cat_names=True))),
                 ('remove_multicollinearity',
                  TransformerWrapper(exclude=[],
                                     transformer=RemoveMulticollinearity(threshold=0.9))),
                 ('transformation',
                  TransformerWrapper(transformer=PowerTransformer(standardize=False))),
                 ('normali

# Modelos - Tunning

### Modelo 1

In [5]:
modelPAR = load_model('baseModels/PassiveAggressiveRegressor')

Transformation Pipeline and Model Successfully Loaded


In [6]:
gridPAR = {
    'C': [0.01, 0.1, 1.0, 2.0, 3.0, 4.0, 5.0, 6.1, 7.0, 8.0, 9.0, 10.0],
    'epsilon': [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'max_iter': [1000, 2000, 3000],
    'tol': [1e-3, 1e-4, 1e-5],
    'validation_fraction': [0.1, 0.2, 0.3],
    'n_iter_no_change': [5, 10, 15]
}

In [7]:
fitModelPAR=tune_model(modelPAR,custom_grid=gridPAR, optimize='MAPE')

ValueError: _CURRENT_EXPERIMENT global variable is not set. Please run setup() first.

In [9]:
predict_model(fitModelPAR)

ValueError: data parameter may not be None without running setup() first.

#### Final model and save

In [ ]:
finalPAR = finalize_model(fitModelPAR)
save_model(finalPAR, 'passiveAggressiveRegressorFinal')

### Modelo 2

In [1]:
modelHR = load_model('baseModels/HuberRegressor')

NameError: name 'load_model' is not defined

In [ ]:
gridHR = {
    'alpha': [0.0001, 0.001, 0.01, 0.1, 1.0],
    'epsilon': [1.35, 1.5, 1.75, 2.0],
    'max_iter': [100, 200, 300, 400, 500],
    'tol': [1e-3, 1e-4, 1e-5]
}

In [ ]:
fitModelHR=tune_model(modelHR, optimize='MAPE')

#### Final model and save

In [ ]:
finalHR = finalize_model(fitModelHR)
save_model(finalHR, 'huberRegressorFinal')

### Modelo 3

In [ ]:
modelETR = load_model('baseModels/ExtraTreesRegressor')

In [ ]:
gridETR = {
    'n_estimators': [50, 100, 200, 300],
    'max_depth': [None, 10, 20, 30],
    'min_samples_split': [2, 5, 10],
    'min_samples_leaf': [1, 2, 4],
    'bootstrap': [True, False]
}

In [ ]:
fitModelETR=tune_model(modelETR,optimize='MAPE')

#### Final model and save

In [ ]:
finalETR = finalize_model(fitModelETR)
save_model(finalETR, 'extraTreesRegressorFinal')

# Predicciones

## Predicciones Modelo 1

In [ ]:
pred_unseen = predict_model(models, data=data_unseen)
print(pred_unseen.head())

## Predicciones Modelo 2

## Predicciones Modelo 3

In [ ]:
!mlflow ui --port 5000